# <center>**RADIOMICS EXTRACTION - First** ***Dummy*** **Extraction - STAPES**</center>

(*Step 3*)

## **Radiomics Workflow:**
  
  **1. Download** DICOM images and convert to **NRRD.**

  **2.** Perform **target segmentations** and save in **NRRD.**
  
  **3.** Perform a **first Radiomic Feature** ***Dummy*** **Extraction,** to:
    
  - Detect **erros in segmentations**: only one dimension, no label 1, only one segmented voxel...
  - Analyze **bin width**.


  **4. Analyze** and **correct mask errors.**

  **5. Adjust bin width.**
   - **Tune featureextractor param file.**


  **6.** Perform **final Radiomic Feature Extraction.**

  **7. Clean Radiomic Features.**

  **8. Merge** with **labels** and **clinical data.**

  **9. Descriptive Statistics.**

  **10. Inferential Statistics.**

  **11. Machine Learning.**

## **FIRST RADIOMIC FEATURE** ***DUMMY*** **EXTRACTION - STAPES**

This notebook is designed to **perform a fisrt radiomic extraction**, to detect **errors in segmentations** and **analyze bin width**. The steps which are followed are:

0.   Environment **configuration**.
1.   **Get image and segmentation** paths.
2.   **Extract radiomic features.**
3.   **Save radiomic features extraction.**
4.   **Check invalid masks.**

In [1]:
# Install libraries
#pip install -q pyradiomics trimesh

In [2]:
# Import libraries
import warnings
import os
import re
from radiomics import featureextractor
import scipy # for filters
import trimesh # for filters
from tqdm import tqdm
import pandas as pd

### **0. Environment configuration.**

In [3]:
warnings.filterwarnings('ignore')

#### Set the working directory

In [4]:
# Set working directory
wd = '/Users/pablomenendezfernandez-miranda/Proyecto Otosclerosis/'
os.chdir(wd)

print(f'Directorio actual: {os.getcwd()}')

# Check directory files
print(f'Directory files: {os.listdir(wd)}')

Directorio actual: /Users/pablomenendezfernandez-miranda/Proyecto Otosclerosis
Directory files: ['Tables', 'Databases', 'Episodes', 'Figures', 'Notebooks']


#### Mount Drive (if executed on Google Colab)

In [5]:
#from google.colab import drive
#drive.mount('/content/drive')

### **1. Get image and segmentation paths**

In [6]:
# Search for images and segmentations

dir= 'Episodes/'
patron = re.compile(r'.*(\d+)\.nrrd$')

images =               [imagen for imagen in os.listdir(dir) if patron.match(imagen)]
segmentations_STAPES = [seg for seg in os.listdir (dir) if 'STAPES' in seg]
segmentations_AF =     [seg for seg in os.listdir (dir) if 'AF' in seg]
segmentations_OW =     [seg for seg in os.listdir (dir) if 'OW' in seg]

print('N imagenes:', len(images))
print('N segmentation STAPES:', len(segmentations_STAPES))
print('N segmentation AF:', len(segmentations_AF))
print('N segmentation OW:', len(segmentations_OW))

N imagenes: 99
N segmentation STAPES: 99
N segmentation AF: 99
N segmentation OW: 99


In [7]:
# Check that each image goes with its segmentations
images.sort()
segmentations_STAPES.sort()
segmentations_AF.sort()
segmentations_OW.sort()

for image, segmentation_STAPES, segmentation_AF, segmentation_OW in zip (images, segmentations_STAPES, segmentations_AF, segmentations_OW):

    # Check segmentation paths
    if int(image[4:8]) == int(segmentation_STAPES[4:8]) and int(image[4:8]) == int(segmentation_AF[4:8]) == int(segmentation_OW[4:8]):
        verification= 'checked!'
    else:
        verification= '....... error!'
        
    print(f' {image} --- {segmentation_STAPES} --- {segmentation_AF} --- {segmentation_OW} --- {verification}')

 EPI_0001.nrrd --- EPI_0001_STAPES.nrrd --- EPI_0001_AF.nrrd --- EPI_0001_OW.nrrd --- checked!
 EPI_0002.nrrd --- EPI_0002_STAPES.nrrd --- EPI_0002_AF.nrrd --- EPI_0002_OW.nrrd --- checked!
 EPI_0003.nrrd --- EPI_0003_STAPES.nrrd --- EPI_0003_AF.nrrd --- EPI_0003_OW.nrrd --- checked!
 EPI_0004.nrrd --- EPI_0004_STAPES.nrrd --- EPI_0004_AF.nrrd --- EPI_0004_OW.nrrd --- checked!
 EPI_0005.nrrd --- EPI_0005_STAPES.nrrd --- EPI_0005_AF.nrrd --- EPI_0005_OW.nrrd --- checked!
 EPI_0006.nrrd --- EPI_0006_STAPES.nrrd --- EPI_0006_AF.nrrd --- EPI_0006_OW.nrrd --- checked!
 EPI_0007.nrrd --- EPI_0007_STAPES.nrrd --- EPI_0007_AF.nrrd --- EPI_0007_OW.nrrd --- checked!
 EPI_0008.nrrd --- EPI_0008_STAPES.nrrd --- EPI_0008_AF.nrrd --- EPI_0008_OW.nrrd --- checked!
 EPI_0009.nrrd --- EPI_0009_STAPES.nrrd --- EPI_0009_AF.nrrd --- EPI_0009_OW.nrrd --- checked!
 EPI_0012.nrrd --- EPI_0012_STAPES.nrrd --- EPI_0012_AF.nrrd --- EPI_0012_OW.nrrd --- checked!
 EPI_0014.nrrd --- EPI_0014_STAPES.nrrd --- EPI_00

### **2. Extract radiomic features**

In [8]:
# Select a sample for dummy extraction
n= 52
sample_images = images[:n]
sample_segmentations_STAPES = segmentations_STAPES[:n]
sample_segmentations_AF = segmentations_AF[:n]
sample_segmentations_OW = segmentations_OW[:n]

In [9]:
# Extraction with segmentation_STAPES

images_= sample_images
segmentations_= sample_segmentations_STAPES

features_list= []
error_list= []

params= 'Notebooks/param_files/param_file.yaml'
extractor= featureextractor.RadiomicsFeatureExtractor(params, verbose=False) #params are optional
#extractor= featureextractor.RadiomicsFeatureExtractor(verbose=False) #params are optional

for i in tqdm(range(len(images_)), desc='Processing images'):

  image_dir= os.path.join(dir, images_[i])
  segmentation_dir= os.path.join(dir, segmentations_[i])

  #print('\n')
  #print(f'{images_[i]} - {segmentations_[i]}')
  #print('Extracting features...')

  try:
    features= extractor.execute(image_dir, segmentation_dir, voxelBased=False)
    image_segmentation_features= (images_[i], segmentations_[i], features)
    features_list.append(image_segmentation_features)
    #print('Done!')
  except Exception as e:
    image_segmentation= (images_[i], segmentations_[i], e)
    error_list.append(image_segmentation)
    #print('Error')
    #print(e)

Processing images: 100%|████████████████████████| 52/52 [07:36<00:00,  8.79s/it]


In [10]:
# Build a DataFrame
segmentations_list= [segmentation for name, segmentation, features_ in features_list]
features_dict_list= [features_ for name, segmentation, features_ in features_list]

df_features= pd.DataFrame(data=[features_ for name, segmentation, features_ in features_list],
                          index=[segmentation for name, segmentation, features_ in features_list])

df_features.index.rename('Image_Segmentation', inplace=True)
#df_features.insert(loc=0, column='label', value=9999, allow_duplicates=False)

print(df_features.shape)
df_features.head()

(42, 2053)


diagnostics_Versions_PyRadiomics  \
Image_Segmentation                                      
EPI_0001_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0002_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0003_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0005_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0007_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   

                     diagnostics_Versions_Numpy  \
Image_Segmentation                                
EPI_0001_STAPES.nrrd                     1.26.4   
EPI_0002_STAPES.nrrd                     1.26.4   
EPI_0003_STAPES.nrrd                     1.26.4   
EPI_0005_STAPES.nrrd                     1.26.4   
EPI_0007_STAPES.nrrd                     1.26.4   

                     diagnostics_Versions_SimpleITK  \
Image_Segmentation                                    
EPI_0001_STAPES.nrrd                          2.4.0   
EPI_0002_STAPES.nrrd                          2.4.0   
EPI_0003_STAPES.nrrd                          2.4.0   
EPI_0005_STAPES.nrrd                          2.4.0   
EPI_0007_STAPES.nrrd                          2.4.0   

                     diagnostics_Versions_PyWavelet  \
Image_Segmentation                                    
EPI_0001_STAPES.nrrd                          1.7.0   
EPI_0002_STAPES.nrrd                          1.7.0   
EPI_0003_STAPES.nrrd                          1.7.0   
EPI_0005_STAPES.nrrd                          1.7.0   
EPI_0007_STAPES.nrrd                          1.7.0   

                     diagnostics_Versions_Python  \
Image_Segmentation                                 
EPI_0001_STAPES.nrrd                      3.12.4   
EPI_0002_STAPES.nrrd                      3.12.4   
EPI_0003_STAPES.nrrd                      3.12.4   
EPI_0005_STAPES.nrrd                      3.12.4   
EPI_0007_STAPES.nrrd                      3.12.4   

                                     diagnostics_Configuration_Settings  \
Image_Segmentation                                                        
EPI_0001_STAPES.nrrd  {'minimumROIDimensions': 2, 'minimumROISize': ...   
EPI_0002_STAPES.nrrd  {'minimumROIDimensions': 2, 'minimumROISize': ...   
EPI_0003_STAPES.nrrd  {'minimumROIDimensions': 2, 'minimumROISize': ...   
EPI_0005_STAPES.nrrd  {'minimumROIDimensions': 2, 'minimumROISize': ...   
EPI_0007_STAPES.nrrd  {'minimumROIDimensions': 2, 'minimumROISize': ...   

                            diagnostics_Configuration_EnabledImageTypes  \
Image_Segmentation                                                        
EPI_0001_STAPES.nrrd  {'Original': {'binWidth': 6.0}, 'Square': {'bi...   
EPI_0002_STAPES.nrrd  {'Original': {'binWidth': 6.0}, 'Square': {'bi...   
EPI_0003_STAPES.nrrd  {'Original': {'binWidth': 6.0}, 'Square': {'bi...   
EPI_0005_STAPES.nrrd  {'Original': {'binWidth': 6.0}, 'Square': {'bi...   
EPI_0007_STAPES.nrrd  {'Original': {'binWidth': 6.0}, 'Square': {'bi...   

                               diagnostics_Image-original_Hash  \
Image_Segmentation                                               
EPI_0001_STAPES.nrrd  1310b8441367f403dccd0241fde06dd70966c56a   
EPI_0002_STAPES.nrrd  64fb22f54e86a46714e45ec0a26705a81f50b639   
EPI_0003_STAPES.nrrd  c37a6f6b17a1a89cd5f06d640fb8e33dc6219c6e   
EPI_0005_STAPES.nrrd  3f11e7a4b9e487bfc8299630acbc69287f745d63   
EPI_0007_STAPES.nrrd  c459b5038a7520ab9b568557367f62b5f88bd8ff   

                     diagnostics_Image-original_Dimensionality  \
Image_Segmentation                                               
EPI_0001_STAPES.nrrd                                        3D   
EPI_0002_STAPES.nrrd                                        3D   
EPI_0003_STAPES.nrrd                                        3D   
EPI_0005_STAPES.nrrd                                        3D   
EPI_0007_STAPES.nrrd                                        3D   

                                     diagnostics_Image-original_Spacing  ...  \
Image_Segmentation                                                  

In [11]:
# PRINT FULL DATAFRAME

def df_show_full(show):
  if show == True:
    pd.set_option('display.max_rows', None)
    pd.set_option('display.max_columns', None)
  if show == False:
    pd.reset_option('display.max_rows')
    pd.reset_option('display.max_columns')

In [12]:
df_show_full(True)
df_features

diagnostics_Versions_PyRadiomics  \
Image_Segmentation                                      
EPI_0001_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0002_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0003_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0005_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0007_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0008_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0014_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0015_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0019_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0020_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0021_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0022_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0023_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0024_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0025_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0027_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0028_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0029_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0031_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0032_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0034_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0035_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0037_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0038_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0040_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0041_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0042_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0047_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0048_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0051_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0056_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0057_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0060_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0061_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0062_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0063_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0064_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0066_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0067_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0068_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0069_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   
EPI_0071_STAPES.nrrd          3.1.0a2.post14+gaab3c6f   

                     diagnostics_Versions_Numpy  \
Image_Segmentation                                
EPI_0001_STAPES.nrrd                     1.26.4   
EPI_0002_STAPES.nrrd                     1.26.4   
EPI_0003_STAPES.nrrd                     1.26.4   
EPI_0005_STAPES.nrrd                     1.26.4   
EPI_0007_STAPES.nrrd                     1.26.4   
EPI_0008_STAPES.nrrd                     1.26.4   
EPI_0014_STAPES.nrrd                     1.26.4   
EPI_0015_STAPES.nrrd                     1.26.4   
EPI_0019_STAPES.nrrd                     1.26.4   
EPI_0020_STAPES.nrrd                     1.26.4   
EPI_0021_STAPES.nrrd                     1.26.4   
EPI_0022_STAPES.nrrd                     1.26.4   
EPI_0023_STAPES.nrrd                     1.26.4   
EPI_0024_STAPES.nrrd                     1.26.4   
EPI_0025_STAPES.nrrd                     1.26.4   
EPI_0027_STAPES.nrrd                     1.26.4   
EPI_0028_STAPES.nrrd                     1.26.4   
EPI_0029_STAPES.nrrd                     1.26.4   
EPI_0031_STAPES.nrrd                     1.26.4   
EPI_0032_STAPES.nrrd                     1.26.4   
EPI_0034_STAPES.nrrd                     1.26.4   
EPI_0035_STAPES.nrrd                     1.26.4   
EPI_0037_STAPES.nrrd                     1.26.4   
EPI_0038_STAPES.nrrd                     1.26.4   
EPI_0040_STAPES.nrrd                     1.26.4   
EPI_0041_STAPES.nrrd                     1.26.4   
EPI_0042_STAPES.nrrd                     1.26.4   
EPI_0047_STAPES.nrrd             

### **3. Save radiomic features extraction**

In [13]:
# Save data
save_path= 'Databases/'
df_features.to_csv(save_path + '3_1_df_radiomics_STAPES_dummy_features.csv')

### **4. Check invalid masks**

In [14]:
# Check invalid masks
print(f'Number of errors: {len(error_list)}')
print(f'\n Image            | Mask                 | Error')
print(f' ----------------  --------------------   --------------------')
for error in error_list: print(error)

Number of errors: 10

 Image            | Mask                 | Error
 ----------------  --------------------   --------------------
('EPI_0004.nrrd', 'EPI_0004_STAPES.nrrd', ValueError('mask has too few dimensions (number of dimensions 1, minimum required 2)'))
('EPI_0006.nrrd', 'EPI_0006_STAPES.nrrd', RuntimeError('Exception thrown in SimpleITK LabelShapeStatisticsImageFilter_GetBoundingBox: /Users/runner/work/SimpleITK/SimpleITK/bld/ITK-prefix/include/ITK-5.4/itkLabelMap.hxx:122:\nITK ERROR: LabelMap(0x7fcb9f048ca0): No label object with label 1.'))
('EPI_0009.nrrd', 'EPI_0009_STAPES.nrrd', ValueError('mask has too few dimensions (number of dimensions 1, minimum required 2)'))
('EPI_0012.nrrd', 'EPI_0012_STAPES.nrrd', ValueError('mask only contains 1 segmented voxel! Cannot extract features for a single voxel.'))
('EPI_0016.nrrd', 'EPI_0016_STAPES.nrrd', ValueError('mask has too few dimensions (number of dimensions 1, minimum required 2)'))
('EPI_0026.nrrd', 'EPI_0026_STAPES.nrrd',